In [1]:
from itertools import combinations, chain
import math

# inputs and processes a list of planar, 4-valent graphs from plantri55 into PD code

def text_to_PD(filename):
    result = []
    
    # Open the file and read lines
    with open(filename, 'r') as file:
        lines = file.readlines()
    
    # Process each line
    for line in lines:
        parts = line.strip().split()
        
        # Find the indices of the first and second numerical entries
        second_num_index = next(i for i, part in enumerate(parts[1:]) if part.isdigit()) + 1
        
        # Extract ASCII strings (between first and second numbers)
        ascii_strings = parts[1:second_num_index]
        
        # Convert ASCII strings to list of numbers based on alphabetical order
        numbers_list = []
        for ascii_str in ascii_strings:
            numbers = [ord(char.lower()) - ord('a') + 1 for char in ascii_str]
            numbers_list.append(numbers)
        
        result.append(numbers_list)
    return result


# gives all lists resulting from changing at most half the signs of the entries of a given list

def change_signs(lst):
    n = len(lst)
    max_flips = math.ceil(n / 2)
    
    # Generate all combinations of indices for flipping signs
    indices = range(n)
    all_combinations = chain.from_iterable(combinations(indices, r) for r in range(max_flips + 1))
    
    # Create a set to store unique results
    result_set = set()
    
    for combo in all_combinations:
        new_lst = lst[:]
        for index in combo:
            new_lst[index] *= -1
        result_set.add(tuple(new_lst))
    
    # Convert set back to list of lists
    result_list = [list(tup) for tup in result_set]
    
    return result_list

# converts a list of PD codes for links to DT codes for corresponding alternating knots

def PD_to_DT_alt(PD_links):
    DT_alt_knots = [[abs(x) for x in list(snappy.Link(L).DT_code()[0])] for L in PD_links if len(snappy.Link(L).DT_code()) == 1]
    return DT_alt_knots

# converts a list of PD codes for alternating knots to a DT codes for all associated non-alternating knots

def PD_to_DT_nonAlt(PD_links):
    alt_knots = [[abs(x) for x in list(snappy.Link(L).DT_code()[0])] for L in PD_links if len(snappy.Link(L).DT_code()) == 1]
    nonAlt_knots = [change_signs(x) for x in alt_knots]
    nonAlt_knots_flatten = [item for sublist in nonAlt_knots for item in sublist]
    return nonAlt_knots_flatten

In [2]:
# converts short DT code to long DT code

def convert_DT(shortDT):
    abs_vals = [abs(x) for x in shortDT]
    signs = [1 if x>0 else -1 for x in shortDT]
    odds = [(2*abs_vals.index(x)+1)*(-signs[abs_vals.index(x)]) for x in range(2,2*len(abs_vals)+2,2)]
    DT = [item for sublist in zip(shortDT, odds) for item in sublist]
    return DT

# converts long DT code to short DT code

def convert_back(longDT):
    return [longDT[i] for i in range(0,len(longDT),2)]

# permutes labels in long DT code

def permute_DT(longDT):
    n = len(longDT)
    newDT = [0]*n
    for i in range(0,n):
        if longDT[(i+1)%n]>0:
            newDT[i] = (longDT[(i+1)%n]-2)%n+1
        else:
            newDT[i] = -((abs(longDT[(i+1)%n])-2)%n+1)
    return newDT

# returns all long DT codes corresponding to a given long DT code diagram

def all_DT(longDT):
    n = len(longDT)
    allDT = [longDT]
    for i in range(n/2-1):
        allDT.append(permute_DT(allDT[-1]))
    return allDT

# runs the roller-coaster algorithm on a given long DT code, returning a sequence of 'over' and 'under'

def coaster_markings(longDT):
    n = len(longDT)
    marking = []
    for i in range(n):
        if abs(longDT[i]) > i+1:
            if longDT[i]<0:
                marking = marking + ['over']
            else:
                marking = marking + ['under']
    return marking

# given a short DT code, runs every roller-coaster algorithm, recording the fewest changes required

def check_all_codes(shortDT):
    longDT = convert_DT(shortDT)
    n = len(longDT)
    allDT = all_DT(longDT)
    best = 100
    for DT in allDT:
        check = coaster_markings(DT)
        best = min(check.count('over'),check.count('under'),best)
    return best

# returns the lowest RCU number among a list of short DT code knots

def best_RC(DT_list):
    best = 100
    for x in DT_list:
        newRC = check_all_codes(x)
        if newRC < best:
            best = newRC
        else:
            continue
    return best

In [3]:
import snappy
# %gui tk

#converts a short DT to a SnapPy knot

def find_knot(DT):
    DT_string = f'DT:{[tuple(DT)]}'
    knot = snappy.Link(DT_string)
    return knot

# returns RC unknottings for a list of knots

def find_RCs(DT_list):
    knots = []
    for x in DT_list:
        best = check_all_codes(x)
        knot = find_knot(x)
        knots = knots + [[best,knot.exterior().identify(),x]]
    return knots

# picks optimal RC unknottings from a list

def opt_RCs(DT_list):
    RC_list = find_RCs(DT_list)
    result = {}
    for sublist in RC_list:
        a, b, c = sublist
        if str(b) not in result or a < result[str(b)][0]:
            result[str(b)] = (a, sublist)
    filtered_list = [entry[1] for entry in result.values()]
    return filtered_list

In [4]:
import pandas as pd

#exports a list of lists to excel

def export_to_excel(list_of_lists, file_name):
    # Convert list of lists to a DataFrame
    df = pd.DataFrame(list_of_lists)
    # Write DataFrame to Excel file
    df.to_excel(file_name, index=False, header=False)
    # index and header are set to False to exclude row and column headers

In [ ]:
import time
start_time = time.time()

# outputs the lowest RCU number among all alternating diagrams of a given crossing number

for crossNum in range(17,18):
    print([crossNum,best_RC(PD_to_DT_alt(text_to_PD(f'graphs{crossNum}.txt'))),f"Elapsed time: {(time.time() - start_time)/60} minutes"])

# [6, 2, 'Elapsed time: 0.00020783344904581706 minutes']
# [7, 2, 'Elapsed time: 0.0003898342450459798 minutes']
# [8, 2, 'Elapsed time: 0.0011523683865865071 minutes']
# [9, 3, 'Elapsed time: 0.0030190626780192058 minutes']
# [10, 3, 'Elapsed time: 0.010344882806142172 minutes']
# [11, 3, 'Elapsed time: 0.04400281508763631 minutes']
# [12, 3, 'Elapsed time: 0.21427689790725707 minutes']
# [13, 4, 'Elapsed time: 1.1200237671534221 minutes']
# [14, 4, 'Elapsed time: 5.09128714799881 minutes']
# [15, 4, 'Elapsed time: 27.773158462842304 minutes']
# [16, 4, 'Elapsed time: 160.6244838833809 minutes']


In [ ]:
# exports all alternating roller-coasters to excel for given crossing number

for crossNum in range(6,17):
    export_to_excel(opt_RCs(PD_to_DT_alt(text_to_PD(f'graphs{crossNum}.txt'))),f"alt_{crossNum}_RCs.xlsx")

In [5]:
# exports all non-alternating roller-coasters to excel for given crossing number

for crossNum in range(6,12):
    export_to_excel(opt_RCs(PD_to_DT_nonAlt(text_to_PD(f'graphs{crossNum}.txt'))),f"nonAlt_{crossNum}_RCs.xlsx")